# TP4b - Kolmogorov Complexity

In [1]:
import numpy as np
import pandas as pd
import gzip
import pickle
from sklearn.datasets import load_diabetes
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.svm import SVR
from sklearn.neighbors import KNeighborsRegressor
from sklearn.metrics import mean_squared_error

In this exercise, you will explore how compression algorithms can be used to approximate the Kolmogorov complexity of datasets and learning tasks.



Kolmogorov complexity $K(x)$ of an object $x$ (typically a string) is the length of the shortest possible program that can produce that object $x$ as output. Unfortunately it is an uncomputable quantity in the general case, but we can approximate it using practical compression tools such as zip. The compressors exploit patterns, redundancy, and structure in data — just as machine learning models do.

This connection leads to a fascinating interpretation: learning can be viewed as compression. In both unsupervised and supervised learning, the goal is to describe data as compactly as possible, either by identifying structure in the data itself or by predicting labels from features.

In [2]:
# Load dataset
data = load_diabetes()
X, y = data.data, data.target
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

Upper bounds of the Kolmogorov complexity $K$ can be obtained by considering various encoders (=compressors). Given an encoder $h$, and data $x$ to compress, the bound on $K(x)$ is given by the size of the compressed data $h(x)$ + the size of the decoder $h^{-1}$, since one needs to describe both of them to re-generate the original data. 

Indeed, given data $x$ to encode (e.g. whole Wikipedia), imagine an encoder that associates that particular $x$ to just one bit, and applies zip otherwise (i.e. to any other string). The encoding of $x$ will be very short, but it is just because $x$ is actually stored in the decoder.

Moreover, in the case of lossy encoders, i.e. that are not lossless (e.g., jpg encoder for images, or machine learning models in general), then one has to take into account that the decoder $h^{-1}$ will not produce the original data $x$ but a corrupted version $x' = h^{-1} \circ h(x)$ (note the slight abuse of notation: $h^{-1}$ is the decoder, not exactly matching the encoder $h$ as the latter is not injective, so in general $h^{-1} \circ h \neq Id$). Therefore, one needs in plus to describe the residuals $z = x'-x$, in order to be able to generate the original data *exactly*. Given the decoded reconstruction $x'$, describing $z$ or $x$ is equivalent. The associated description cost is $K(z|x') = K(z|h^{-1}, h(x)) = K(x|h^{-1}, h(x))$.

As a result, in the general case we have:
$$ K(x) \leq K(h^{-1}) + K( h(x) ) + K(x|h^{-1}, h(x))$$
that is, the cost of describing the decoder, the cost of describing the encoded data (which is upper bounded by its length + twice its $\log$), and the cost of describing residuals if the encoder is lossy.


Note that Kolmogorov complexity does not include any computational complexity consideration (all programs, whether fast or very slow, are treated equally).



In `unsupervised learning`, we are primarily interested in describing the structure of the data itself, such as clustering or density estimation. The goal is to find the shortest description of the dataset $x$. Considering lossless compression only, there is no residuals to describe. Thus, we have for instance:
$$ K(x) \leq |\text{zip}(x)| + |\text{unzip program}|$$

In `supervised learning`, we do not only describe the inputs $x$, but also learn a predictor, i.e. a mapping from $x$ to the labels $y$, which makes mistakes. Here, the goal is to describe $y$ given $x$, using a model $h$. We will consider that for any sample $x_i$, the model outputs a distribution of probability $p_h(y|x_i)$ over possible labels. As the inputs $x$ are given to the predictor, they do not need to be encoded, and in the Kolmogorov complexity, only two terms remain: the description of the model (seen as a decoder) and the description of the true labels $y$ given the predictions $p_h(y|x_i)$ (similarly to residuals):
$$ K(y|x) \leq K(h) + K(y|h,x) $$
where $K(y|h,x)$ stands for the log likelihood error of our model (over the whole dataset) given the data $x$, that is, $\sum_i -\log p_h(y_i|x_i)$, which is precisely the number of bits of information one should give to identify, for each input sample $x_i$, the true label $y_i$ given the prediction $p_h(y_i|x_i)$ of the model.

This machine learning instanciation of the Kolmogorov complexity is named the _Minimum Description Length (MDL)_ paradigm.

The Kolmogorov complexity $K(h)$ of the model itself can be approximated using the Bayesian Information Criterion (BIC) or the Akaike Information Criterion (AIC), based on the number of parameters of the models (and possibly the number of samples).

## Practical
1. Use `gzip` to compute a Kolmogorov complexity upper bound, assuming an unsupervised task on the dataset features. The data should be turned into binary first using pickle.

2. Train the models given on the dataset.

3. Use the trained models to compute Kolmogorov complexity upper bounds in the supervised setting. For MDL you should consider both the Bayesian and Akaike criterions. It is up to you to find the correct number of parameters for its model.

4. How do the upper bounds compare between the different supervised models? Explain your answer.

In [3]:
# Initialize Models
models = {
    "Linear Regression": LinearRegression(),
    "Decision Tree": DecisionTreeRegressor(),
    "Support Vector Machine": SVR(),
    "k-Nearest Neighbors": KNeighborsRegressor()
}

# Function to compute compressed size as Kolmogorov complexity approximation
def compute_compressed_size(obj):
    # TODO: find the length of a compressed object
    # ...
    #
    pass

# TODO: compute Kolmogorov complextiy upper bounds
# ...
#

Remember that in the supervised case we ommit the complexity of the data itself. This is because we are not interested in compressing the data, but rather in compressing the labels given the data. However, in order to have a fair comparisson with the unsupervised case, we will add this complexity to the mix. Thus, the consider upper bounds on the joint distribution $(x,y)$ instead of $y|x$:
$$ K(x,y) \leq K(h) + K(x) + K(y|h,x)$$
and we approximate $K(x)$ by $|\text{zip}(x)| $.

5. Recompute the upper bound in the supervised case using the new formula.

6. Now that the results are comparable, how do the upper bounds behave between the supervised and the unsupervised setting?

7. Why is the zip compression so bad when dealing with tabular data?

8. What are the assumptions behind using AIC and BIC for estimating the description length of a model? What types of models or settings might violate these assumptions?

9. In the supervised setting, why is it important to separate the complexity of the model from the complexity of the residuals? What does this decomposition tell us ?